In [ ]:
# ======================================================
# CELLULE 2 — MODELE MLP MULTI-LABEL (INCHANGE)
# ======================================================
import numpy as np
import pickle
from sklearn.model_selection import train_test_split, GridSearchCV, KFold
from sklearn.preprocessing import StandardScaler
from sklearn.neural_network import MLPClassifier
from sklearn.multiclass import OneVsRestClassifier
from sklearn.metrics import hamming_loss, f1_score
import joblib



X = np.load("/kaggle/input/dataset-pre-traitement-sift-bovw-pca/X_pca.npy")
y = np.load("/kaggle/input/dataset-pre-traitement-sift-bovw-pca/y.npy")


with open("/kaggle/input/dataset-pre-traitement-sift-bovw-pca/label_names.pkl", "rb") as f:
    label_names = pickle.load(f)

print(X.shape, y.shape)


X_train, X_test, y_train, y_test = train_test_split(
    X, y, test_size=0.2, random_state=42
)
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
# =============================
# MLP + OneVsRest (INCHANGE)
# =============================
mlp = MLPClassifier(
    hidden_layer_sizes=(200,100,50),
    activation='relu',
    alpha=0.0005,
    learning_rate_init=0.001,
    max_iter=500,
    early_stopping=True,
    n_iter_no_change=20,
    random_state=42,
    verbose=True
)
ovr = OneVsRestClassifier(mlp, n_jobs=-1)
# =============================
# GRID SEARCH (INCHANGE)
# =============================
param_grid = {
    'estimator__hidden_layer_sizes': [(100,50), (200,100,50)],
    'estimator__alpha': [0.0001, 0.0005, 0.001],
    'estimator__learning_rate_init': [0.001, 0.005]
}
cv = KFold(n_splits=2, shuffle=True, random_state=42)
grid = GridSearchCV(
    ovr,
    param_grid=param_grid,
    cv=cv,
    scoring='f1_micro',
    n_jobs=-1,
    verbose=2
)
grid.fit(X_train_scaled, y_train)
print("\n===== Meilleurs paramètres =====")
print(grid.best_params_)

# PREDICTION + SEUIL

y_pred_prob = grid.predict_proba(X_test_scaled)
threshold = 0.3
y_pred = (y_pred_prob >= threshold).astype(int)

# EVALUATION

hamming = hamming_loss(y_test, y_pred)
f1_micro = f1_score(y_test, y_pred, average='micro', zero_division=0)
f1_macro = f1_score(y_test, y_pred, average='macro', zero_division=0)
subset_acc = np.all(y_pred == y_test, axis=1).mean()
print("\n Évaluation MLP Multi-label Optimisé ")
print("Hamming Loss :", hamming)
print("F1 micro :", f1_micro)
print("F1 macro :", f1_macro)
print("Subset Accuracy :", subset_acc)


# SAUVEGARDE MODELE

joblib.dump(grid.best_estimator_, 'mlp_multilabel_model_optim.pkl')
print("\n Modèle MLP sauvegardé")  

(8091, 100) (8091, 495)
Fitting 2 folds for each of 12 candidates, totalling 24 fits
Iteration 1, loss = 0.20203506
Validation score: 0.978395
Iteration 1, loss = 0.11026917
Iteration 1, loss = 0.09336845
Iteration 1, loss = 0.10209629
Validation score: 0.996914
Validation score: 0.996914
Validation score: 0.996914
Iteration 2, loss = 0.01885310
Iteration 2, loss = 0.09485507
Validation score: 0.996914
Iteration 2, loss = 0.01462858
Validation score: 0.978395
Iteration 2, loss = 0.01578347
Validation score: 0.996914
Validation score: 0.996914
Iteration 3, loss = 0.00673809
Iteration 3, loss = 0.00453424
Iteration 3, loss = 0.07051637
Validation score: 0.996914
Validation score: 0.978395
Validation score: 0.996914
Iteration 3, loss = 0.00803343
Validation score: 0.996914
Iteration 4, loss = 0.00428858
Iteration 4, loss = 0.00340042
Validation score: 0.996914
Iteration 4, loss = 0.05580716
Validation score: 0.978395
Validation score: 0.996914
Iteration 4, loss = 0.00215347
Validation sco

/usr/local/lib/python3.12/dist-packages/joblib/externals/loky/process_executor.py:782: UserWarning: A worker stopped while some jobs were given to the executor. This can be caused by a too short worker timeout or by a memory leak.
  warnings.warn(



Validation score: 0.996914
Iteration 7, loss = 0.00439667
Validation score: 0.996914
Iteration 7, loss = 0.00315883
Validation score: 1.000000
Iteration 7, loss = 0.02967214
Validation score: 0.987654
Iteration 7, loss = 0.00740533
Validation score: 0.996914
Iteration 8, loss = 0.00268909
Validation score: 1.000000
Iteration 8, loss = 0.00382958
Validation score: 0.996914
Iteration 8, loss = 0.02402875
Validation score: 0.987654
Iteration 8, loss = 0.00633698
Validation score: 0.996914
Iteration 9, loss = 0.00233489
Validation score: 1.000000
Iteration 9, loss = 0.00338826
Validation score: 0.996914
Iteration 9, loss = 0.01925356
Validation score: 0.987654
Iteration 10, loss = 0.00215046
Validation score: 1.000000
Iteration 9, loss = 0.00526827
Validation score: 0.996914
Iteration 10, loss = 0.00304348
Validation score: 0.996914
Iteration 10, loss = 0.01548647
Validation score: 0.987654
Iteration 11, loss = 0.00200152
Validation score: 1.000000
Iteration 10, loss = 0.00458342
Validati